# **Capstone Project - The Battle of Neighborhoods**

 **The texts below may have grammar errors. Use Google translator to write them in English, sorry**

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)


## Introduction: Business Problem <a name="introduction"></a>

This project has the purpose of finding an ideal location to build a hospital. Therefore, during this project he will focus on Mexico City, Mexico.

The purpose of this project is to detect the areas where there are no hospitals in the vicinity of the city center. The benefits that can be obtained from selecting a location where there are no hospitals in the surroundings is the one that will be able to provide people with medical attention to people faster and in time to people around them.

It will try to use what you have learned in these latest IBM Data Science courses to try to detect the best possible location for stakeholders. 

## Data <a name="data"></a>

To solve the problem, the following factors will be taken into consideration:

*   number of existing hospitals in the neighborhood
*   number of and distance to hospitals in the neighborhood, if any distance of neighborhood from city center

Following data sources will be needed to extract/generate the required information:


*   The approximate addresses of the locations to be used will be obtained using Google Maps API reverse geocoding
*   The number of hospitals and their location by neighborhood will be obtained using Foursquare API
+   coordinate of Mexico City center will be obtained using Google Maps API geocoding

## **Hospital locations**

Before we start, let's download all the dependencies that we will need.

In [ ]:
pip install geopy

In [ ]:
pip install geocoder

In [ ]:
import json # library to handle JSON files
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

#import yfinance as yf
import requests # library to handle requests
#from bs4 import BeautifulSoup
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import random # library for random number generation
import numpy as np # library for vectorized computation
import pandas as pd # library to process data as dataframes

import geocoder
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans
from sklearn.datasets.samples_generator import make_blobs

import folium # map rendering library

import math

print('Libraries imported.')

/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:144: FutureWarning:

The sklearn.datasets.samples_generator module is  deprecated in version 0.22 and will be removed in version 0.24. The corresponding classes / functions should instead be imported from sklearn.datasets. Anything that cannot be imported from sklearn.datasets is now part of the private API.



Libraries imported.


In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent Course_Project, as shown below.

In [ ]:
geolocator = Nominatim(user_agent="Course_Project")

Let's get the geographical coordinates of Center Mexico City.

In [ ]:
address = 'Zocalo,Mexico City, Mexico'

location = geolocator.geocode(address)
latitude_mex = location.latitude
longitude_mex = location.longitude
print('The geograpical coordinate of Mexico City are latitude {} and longitude {}.'.format(latitude_mex, longitude_mex))

The geograpical coordinate of Mexico City are latitude 19.4322987 and longitude -99.1323909.


### Define Foursquare Credentials and Version

In [ ]:
CLIENT_ID = '2RPTFEGGDZQ0RQ4LRJCLH2BHVXJW4WRHI5J1ORZM3Q3CXKH2' # your Foursquare ID
CLIENT_SECRET = 'C0AE2NHWWEOURYDNTJXVBOR0RGU3EDOWCBYK5WQKJYU3RJ3V' # your Foursquare Secret
ACCESS_TOKEN = 'J4AIQLYWRYYHWK400DT4NPK0G2KXRWL3MIRX15FC3CUWGOHJ' # your FourSquare Access Token

VERSION = '20180605' # Foursquare API version
LIMIT = 150 # A default Foursquare API limit value
radius = 4500

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 2RPTFEGGDZQ0RQ4LRJCLH2BHVXJW4WRHI5J1ORZM3Q3CXKH2
CLIENT_SECRET:C0AE2NHWWEOURYDNTJXVBOR0RGU3EDOWCBYK5WQKJYU3RJ3V


### Create URL and send GET request.

In [ ]:
# Category IDs corresponding to Medical Center were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):
medical_category = '4bf58dd8d48988d196941735'

url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        CLIENT_ID, CLIENT_SECRET, VERSION, latitude_mex, longitude_mex, medical_category, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?client_id=2RPTFEGGDZQ0RQ4LRJCLH2BHVXJW4WRHI5J1ORZM3Q3CXKH2&client_secret=C0AE2NHWWEOURYDNTJXVBOR0RGU3EDOWCBYK5WQKJYU3RJ3V&v=20180605&ll=19.4322987,-99.1323909&categoryId=4bf58dd8d48988d196941735&radius=4500&limit=150'

In [ ]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '609e03c5ae103039660bac67'},
 'response': {'groups': [{'items': [{'reasons': {'count': 0,
       'items': [{'reasonName': 'globalInteractionReason',
         'summary': 'This spot is popular',
         'type': 'general'}]},
      'referralId': 'e-0-4bbf55f5006dc9b62d62fc3f-0',
      'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/building/medical_',
          'suffix': '.png'},
         'id': '4bf58dd8d48988d196941735',
         'name': 'Hospital',
         'pluralName': 'Hospitals',
         'primary': True,
         'shortName': 'Hospital'}],
       'id': '4bbf55f5006dc9b62d62fc3f',
       'location': {'address': 'Avenida Cuauhtémoc, 330',
        'cc': 'MX',
        'city': 'Cuauhtemoc',
        'country': 'México',
        'crossStreet': 'Esq. con Eje 3 Sur (Dr. Ignacio Morones Prieto)',
        'distance': 3558,
        'formattedAddress': ['Avenida Cuauhtémoc, 330 (Esq. con Eje 3 Sur (Dr. Ignacio Morones Pri

In [ ]:
results = requests.get(url).json()
venue = results['response']['groups'][0]['items']
dataframe = json_normalize(venue)
dataframe.head()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: FutureWarning:

pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead



referralId  ...  venue.venuePage.id
0  e-0-4bbf55f5006dc9b62d62fc3f-0  ...                 NaN
1  e-0-4dd7d2a22271c5d36d44329f-1  ...                 NaN
2  e-0-4d10aa865584f04d870b5916-2  ...                 NaN
3  e-0-4e998fca30f8e35f55c26152-3  ...                 NaN
4  e-0-4e1e405914959804e9e0a127-4  ...                 NaN

[5 rows x 22 columns]

In [ ]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['venue.name', 'venue.categories'] + [col for col in dataframe.columns if col.startswith('venue.location.')] + ['venue.id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['venue.categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]

dataframe_filtered
#dataframe_filtered = dataframe_filtered[dataframe_filtered['categories']=='Hospital'].append(dataframe_filtered[dataframe_filtered['categories']=='Medical Center'])
#dataframe_filtered



name  ...                        id
0                    Centro Médico Nacional Siglo XXI  ...  4bbf55f5006dc9b62d62fc3f
1                                   Hospital de Jesús  ...  4dd7d2a22271c5d36d44329f
2                   Hospital Nuestra Señora de la Luz  ...  4d10aa865584f04d870b5916
3   Fundación Conde de Valenciana (Institución de ...  ...  4e998fca30f8e35f55c26152
4                     Hospital De Cardiología CM SXXI  ...  4e1e405914959804e9e0a127
..                                                ...  ...                       ...
95      Hospital General Dr. Gaudencio González Garza  ...  52403128498edca657d94ade
96        Unidad De Consulta Externa C.M.N. "La Raza"  ...  50f6d758e4b0ec3e2e7ecc44
97                                    IMSS UMF No. 11  ...  4c9aa287292a6dcbb5d1d076
98                                Clinica 21 Del IMSS  ...  5035a307e4b0006c00673970
99  UMAE Gineco obstetricia No.3 (Centro Medico Na...  ...  5016ec1ce4b05d9dc97df797

[100 rows x 16 columns]

**NOTE: Mexico City (abbreviated as CDMX and previously known as the Federal District or D. F.)**

In [ ]:
print('Total number of Medical Center:', len(dataframe_filtered))

Total number of Medical Center: 100


In [ ]:
dataframe_filtered.name

0                      Centro Médico Nacional Siglo XXI
1                                     Hospital de Jesús
2                     Hospital Nuestra Señora de la Luz
3     Fundación Conde de Valenciana (Institución de ...
4                       Hospital De Cardiología CM SXXI
                            ...                        
95        Hospital General Dr. Gaudencio González Garza
96          Unidad De Consulta Externa C.M.N. "La Raza"
97                                      IMSS UMF No. 11
98                                  Clinica 21 Del IMSS
99    UMAE Gineco obstetricia No.3 (Centro Medico Na...
Name: name, Length: 100, dtype: object

In [ ]:
hospital_map = folium.Map(location=[latitude_mex, longitude_mex], zoom_start=13) # generate map centred around the Conrad Hotel

# add a red circle marker to represent the Conrad Hotel
folium.CircleMarker(
    [latitude_mex, longitude_mex],
    radius=10,
    color='red',
    popup='Conrad Hotel',
    fill = True,
    fill_color = 'red',
    fill_opacity = 0.6
).add_to(hospital_map)

# add the Hospitals as blue circle markers
for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        color='blue',
        popup=label,
        fill = True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(hospital_map)

# display map
hospital_map

Let's visualizat Mexico City the neighborhoods in it.

## **Neighborhood Candidates**

The latitude and longitude coordinates will be created for the centroids of the neighborhoods to be considered to create the grid of cells within Mexico City, considering a radius for this of 5 km from the city center. The center of Mexico City is the 'Plaza de la Constitución' (Zocalo).

Our neighborhoods will be defined as circular areas with a radius of 500 meters, so our neighborhood centers will be 1000 meters apart

In [ ]:
pip install pyproj

In [ ]:
pip install shapely

In [ ]:
#!pip install shapely
import shapely.geometry

#!pip install pyproj
import pyproj

import math

mex_center = [latitude_mex,longitude_mex]

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Mexico City center longitude={}, latitude={}'.format(mex_center[1], mex_center[0]))
x, y = lonlat_to_xy(mex_center[1], mex_center[0])
print('Mexico City center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Mexico City center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Mexico City center longitude=-99.1323909, latitude=19.4322987
Mexico City center UTM X=-7767792.171651198, Y=15450036.556783177
Mexico City center longitude=-99.13239089995288, latitude=19.432298700004093


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:14: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1



Let's create a hexagonal grid of cells: we offset every other row, and adjust vertical row spacing so that every cell center is equally distant from all it's neighbors.

In [ ]:
mex_center_x, mex_center_y = lonlat_to_xy(mex_center[1], mex_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = mex_center_x - 10000
x_step = 2000
y_min = mex_center_y - 10000 - (int(21/k)*k*1000 - 20000)/2
y_step = 2000 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 1000 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(mex_center_x, mex_center_y, x, y)
        if (distance_from_center <= 10001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:14: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/

### Next, the data of the candidate neighborhoods will be displayed 

In [ ]:
map_mex = folium.Map(location=mex_center, zoom_start=13)
folium.Marker(mex_center, popup='Zocalo').add_to(map_mex)
for lat, lon in zip(latitudes, longitudes): 
    folium.Circle([lat, lon], radius=500, color='red', fill=False, fill_opacity=0.5).add_to(map_mex)

# add the Hospitals as blue circle markers
for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        color='blue',
        popup=label,
        fill = True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(map_mex)

map_mex

The coordinates of the centers of the candidate neighborhoods to be evaluated will be obtained through the OpenStreetMap service

In [ ]:
from geopy.geocoders import Nominatim
from geopy.exc import GeopyError

In [ ]:
def get_coords(saddress):
	try:
		geolocator = Nominatim(user_agent="altaruru_testgeopy")
		location = geolocator.geocode(saddress)
		#print("C# %s %s  ---> %s" % (location.latitude, location.longitude, location.address))
		#print(location.raw)
		return location.latitude, location.longitude
	except:		
		debug.print_exception()
		return None	

def get_address(lan, lon):
	try:
		geolocator = Nominatim(user_agent="altaruru_testgeopy")
		scoord = ("%s %s" % (lan, lon))
		location = geolocator.reverse(scoord)
		#print("A# %s %s  ---> %s" % (location.latitude, location.longitude, location.address))
		#print(location.raw)
		return location.address
	except:		
		debug.print_exception()
		return None

In [ ]:
address = []
for i in range(len(latitudes)):
  try:
    direccion = get_address("{}".format(latitudes[i]),"{}".format(longitudes[i]))
    address.append(direccion)
  except:
    address.append('NO ADDRESS')

address

['Avenida 529, San Juan de Aragón 1a. Sección, U.H. San Juán de Aragón I, Ciudad de México, 07969, México',
 'Calle Norte 94, Ex Escuela de tiro, Gustavo A. Madero, Ciudad de México, 07960, México',
 'Calle Norte 72 A, Gertrudis Sanchez 1a Secc, Gustavo A. Madero, Ciudad de México, 07850, México',
 'Chedraui Tepeyac, Avenida Ferrocarril Hidalgo, Ampliación La Joyita, Gustavo A. Madero, Ciudad de México, 07860, México',
 '606, Calzada de los Misterios, Industrial, Gustavo A. Madero, Ciudad de México, 07800, México',
 'Avenida del Peñón, Peñón de los Baños, Venustiano Carranza, Ciudad de México, 15510, México',
 'Calle Puerto Arturo, Aquiles Serdán, Venustiano Carranza, Ciudad de México, 15430, México',
 'Avenida Río Consulado, Ampliación Simón Bolívar, Venustiano Carranza, Ciudad de México, 15420, México',
 'Avenida Ingeniero Eduardo Molina, La Joya, Gustavo A. Madero, Ciudad de México, 07890, México',
 'Calle Norte 56 A, Emiliano Zapata, Gustavo A. Madero, Ciudad de México, 07889, Méxi

In [ ]:
import pandas as pd

df_locations = pd.DataFrame({'Address': address,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head()

Address  ...  Distance from center
0  Avenida 529, San Juan de Aragón 1a. Sección, U...  ...           9539.392014
1  Calle Norte 94, Ex Escuela de tiro, Gustavo A....  ...           8888.194417
2  Calle Norte 72 A, Gertrudis Sanchez 1a Secc, G...  ...           8660.254038
3  Chedraui Tepeyac, Avenida Ferrocarril Hidalgo,...  ...           8888.194417
4  606, Calzada de los Misterios, Industrial, Gus...  ...           9539.392014

[5 rows x 6 columns]

## Methodology <a name="methodology"></a>

The purpose of this project is to detect the areas where there are no hospitals in the vicinity of the city center. The benefits that can be obtained from selecting a location where there are no hospitals in the surroundings is the one that will be able to provide people with medical attention to people faster and in time to people around them. For this, the search is limited to an approximate radius of 5 km from the city center (Zocalo)

First, information was obtained from the Hospitals within a radius of 5 km from the city center. In addition, the information on the candidate neighborhoods to be considered for the analysis was generated.

Then, the information previously obtained will be analyzed. The density of the hospitals will be observed through heat maps to identify the optimal areas that are 1 km away from another hospital

The locations will be presented through maps where the locations will be grouped by k-means. From this the addresses of the optimal places will be obtained

## Analysis <a name="analysis"></a>

Hospital locations are shown using a heat map to observe their density

In [ ]:
from folium import plugins
from folium.plugins import HeatMap

coord_heat = dataframe_filtered[["lat", "lng"]].to_numpy()

map_mex = folium.Map(location=mex_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_mex) #cartodbpositron cartodbdark_matter
HeatMap(coord_heat,radius=25).add_to(map_mex)
folium.Marker(mex_center).add_to(map_mex)
folium.Circle(mex_center, radius=1000, fill=False, color='white').add_to(map_mex)
folium.Circle(mex_center, radius=2000, fill=False, color='white').add_to(map_mex)
folium.Circle(mex_center, radius=3000, fill=False, color='white').add_to(map_mex)
folium.Circle(mex_center, radius=4000, fill=False, color='white').add_to(map_mex)
folium.Circle(mex_center, radius=5000, fill=False, color='white').add_to(map_mex)

map_mex



The distance and the number of hospitals within a radius of 1000 m from the neighborhood centers are calculated

In [ ]:
def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

def count_hospital_nearby(x, y, dataframe_filtered, radius=2000):    
    count = 0
    for i in range(len(dataframe_filtered)):
        res_x, res_y = lonlat_to_xy(dataframe_filtered.lng[i],dataframe_filtered.lat[i])
     #   res_x = dataframe_filtered.lat[i]; res_y = dataframe_filtered.lng[i]
        d = calc_xy_distance(x, y, res_x, res_y)
        print(d)
        if d<=radius:
            count += 1
    return count

def find_nearest_hospital(x, y, dataframe_filtered):
    d_min = 100000
    for i in range(len(dataframe_filtered)):
        res_x, res_y = lonlat_to_xy(dataframe_filtered.lng[i],dataframe_filtered.lat[i])
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_hospital_counts = []
roi_hospital_distances = []
Ciclo = 0

print('Generating data on location candidates... ', end='')
for x, y in zip(xs, ys):
  Ciclo = Ciclo + 1
  print("Entro en el ciclo numero : ",Ciclo)
  count = count_hospital_nearby(x, y, dataframe_filtered, radius=2000)
  roi_hospital_counts.append(count)
  distance = find_nearest_hospital(x, y, dataframe_filtered)
  roi_hospital_distances.append(distance)
print('done.') 


Generating data on location candidates... Entro en el ciclo numero :  1


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1



16231.99725088811
10143.706971522111


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1



14004.09344304174
12386.353513663056
15701.010628721771


...

13414.573764734274


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotch

done.


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1



"\nprint('Generating data on location candidates... ', end='')\nfor x, y in zip(xs, ys):\n  count, distance = cf_hospital_nearby(x, y, dataframe_filtered, radius=500)\n  roi_hospital_counts.append(count)\n  roi_hospital_distances.append(distance)\nprint('done.') \n"

In [ ]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':latitudes,
                                 'Longitude':longitudes,
                                 'X':xs,
                                 'Y':ys,
                                 'Hospitals nearby':roi_hospital_counts,
                                 'Distance to Hospital':roi_hospital_distances})

df_roi_locations.head(10)

Latitude  Longitude  ...  Hospitals nearby  Distance to Hospital
0  19.452922 -99.091671  ...                 0           4070.237462
1  19.458466 -99.099384  ...                 0           2177.950545
2  19.464010 -99.107100  ...                 1            959.220600
3  19.469556 -99.114819  ...                 0           2257.596010
4  19.475103 -99.122540  ...                 0           2053.761141
5  19.438276 -99.085163  ...                 0           5160.206282
6  19.443816 -99.092874  ...                 0           4072.090640
7  19.449357 -99.100587  ...                 0           2404.723190
8  19.454899 -99.108303  ...                 3           1180.634667
9  19.460442 -99.116022  ...                 2           1299.656605

[10 rows x 6 columns]

In [ ]:
good_hos_count = np.array((df_roi_locations['Hospitals nearby']<=2))
print('Locations with no more than two Hospitals nearby:', good_hos_count.sum())

good_locations = good_hos_count
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]

Locations with no more than two Hospitals nearby: 52
Locations with both conditions met: 52


### Obtained locations are mapped

In [ ]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]
coord_heat = dataframe_filtered[["lat", "lng"]].to_numpy()

map_mex = folium.Map(location=mex_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_mex)
HeatMap(coord_heat,radius=25).add_to(map_mex)
folium.Circle(mex_center, radius=5000, color='white', fill=True, fill_opacity=0.6).add_to(map_mex)
folium.Marker(mex_center).add_to(map_mex)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_mex) 
map_mex

In [ ]:
map_mex = folium.Map(location=mex_center, zoom_start=13)
HeatMap(good_locations, radius=25).add_to(map_mex)
folium.Marker(mex_center).add_to(map_mex)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_mex)
map_mex

The locations will be grouped with the established requirements to create zone centers that contain good locations. 

In [ ]:
from sklearn.cluster import KMeans

number_of_clusters = 20

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_mex = folium.Map(location=mex_center, zoom_start=13)
HeatMap(coord_heat).add_to(map_mex)
folium.Circle(mex_center, radius=5000, color='white', fill=True, fill_opacity=0.5).add_to(map_mex)
folium.Marker(mex_center).add_to(map_mex)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_mex) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_mex)
map_mex

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/

The addresses of these clustered centers will be a good starting point for exploring neighborhoods and finding the best possible location based on the specific characteristics of the neighborhood. 

In [ ]:
map_mex = folium.Map(location=mex_center, zoom_start=13)
folium.Marker(mex_center).add_to(map_mex)
folium.TileLayer('cartodbpositron').add_to(map_mex)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_mex)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_mex)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=600, color='green', fill=False).add_to(map_mex) 
map_mex

The distance of these candidate locations from the city center is calculated

In [ ]:
candidate_area_addresses = []
d = []
coord_addr_lat = []
coord_addr_lon = []

print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address("{}".format(lat),"{}".format(lon))
    geo_addr = geolocator.geocode(addr)
    coord_addr_lat.append(geo_addr.latitude)
    coord_addr_lon.append(geo_addr.longitude)
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(geo_addr.longitude, geo_addr.latitude)
    d.append(calc_xy_distance(x, y, mex_center_x, mex_center_y))

Addresses of centers of areas recommended for further analysis



/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: DeprecationWarning:

This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotch

In [ ]:
print('==============================================================')
print('          Addresses of centers of areas recommended ')
print('==============================================================\n')

for i in range(len(reference)):
  print('{}{} => {:.1f}km from Zocalo'.format(candidate_area_addresses[i], ' '*(150-len(candidate_area_addresses[i])), d[i]/1000))

          Addresses of centers of areas recommended 

Calle Norte 82 A, Gertrudis Sánchez 2a. Sección, Gertrudis Sanchez 2da Secc, Ciudad de México, 07839, México                                           => 9.1km from Zocalo
Calle Luis Moya, Cuauhtémoc, Ciudad de México, 06070, México                                                                                           => 3.1km from Zocalo
Avenida Canal de Tezontle, La Asunción, Iztacalco, Ciudad de México, 08600, México                                                                     => 10.4km from Zocalo
Calle Asistencia Pública, Federal, Venustiano Carranza, Ciudad de México, 15700, México                                                                => 9.5km from Zocalo
Calle del Fresno, Atlampa, Cuauhtémoc, Ciudad de México, 06450, México                                                                                 => 7.7km from Zocalo
Escuela Secundaria Técnica n°47 "Juan de Dios Batiz", Avenida Insurgentes Norte, Tlac

From the above, it was observed that 20 locations were obtained that meet the requirements. They will then be shown on a map

In [ ]:
map_mex = folium.Map(location=mex_center, zoom_start=13)
folium.Circle(mex_center, radius=100, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_mex)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_mex) 
map_mex




## Results and Discussion <a name="results"></a>

From the above, it can be seen that most of the optimal locations in the East of the 5 km x 5 km area from the city center. It was determined that there is a greater concentration of Hospitals in the West and South of the area.

Of the generated neighborhoods, 52 were shown to be optimal to be considered, so it was not chosen to analyze a specific neighborhood and take into account all of them for the analysis. It is known that not all the optimal locations obtained are useful to build a Hospital, however, these locations can serve as a reference point to choose the location to build a Hospital that can guarantee greater access of these to the most remote areas of an existing Hospital.

## Conclusion <a name="conclusion"></a>

The purpose of this project was to find areas where a Hospital could be built that would guarantee greater access to medical services in remote areas. Although it is known that not all of the 20 locations obtained are really viable for the construction of a Hospital, it is expected that they can serve as a reference point for the selection of a suitable area.